#  Birds Location

In this notebook, you may find:
    1. Preprocessing of the data
    2. Interactive and final plotting with Bokeh
        2.a Pipits according to Kasios
        2.b Blue pipits and Kasios birds
        2.C Interactive map with all birds

The image of the map of Lekagul roadways was processed using vectormagic to get a neater picture.

We attempted to use altair for the visualization but as it occurred to us, Vega-lite (and thus altair) does not allow to input images as marks.
We have therefore focused on Bokeh.

### Libraries 

In [1]:
import pandas as pd
import altair as alt
import matplotlib.pyplot as plt
import os
import plotly.offline as offline
import plotly.graph_objs as go
import bokeh
from __future__ import division

import numpy as np
from PIL import Image
from bokeh.plotting import figure, show, output_file, ColumnDataSource
from bokeh.models import ColumnDataSource, LabelSet, Slider, RangeSlider, DateRangeSlider
from bokeh.io import output_file, show, curdoc, output_notebook
from bokeh.layouts import widgetbox, column
from bokeh.models.widgets import Slider
from bokeh.models import Legend
from bokeh.plotting import figure
from bokeh.palettes import Category20
from bokeh.models import Label


In [3]:
path =  "" #path to csv files and map
os.chdir(path)

birds=pd.read_csv('AllBirdsv4.csv')
test_birds=pd.read_csv('Test Birds Location.csv')

# 1.Preprocessing of data

In [4]:
clean_y=[]
for i in birds['Y'].tolist():
    clean_y.append(i.replace('?',""))

birds['Y']=clean_y

#build year feature
birds['Year']=birds['Date'].str[-4:]
birds.loc[birds['Year'].str.contains("-00"),'Year']=birds[birds['Year'].str.contains("-00")]['Date'].str[:4]
birds.loc[birds['Year'].str.contains("0000"),'Year']="2000" #when there is no date
birds['Year'] = birds['Year'].apply(pd.to_numeric)

# 2.Plotting with bokeh

## 2.1 Pipits located by Kasios

In [27]:
# Open image, and make sure it's RGB*A*
lena_img = Image.open('Lekagul_very_neat.png').convert('RGBA')
xdim, ydim = lena_img.size
print("Dimensions: ({xdim}, {ydim})".format(**locals()))
# Create an array representation for the image `img`, and an 8-bit "4
# layer/RGBA" version of it `view`.
img = np.empty((ydim, xdim), dtype=np.uint32)
view = img.view(dtype=np.uint8).reshape((ydim, xdim, 4))
# Copy the RGBA image into view, flipping it so it comes right-side up
# with a lower-left origin
view[:,:,:] = np.flipud(np.asarray(lena_img))

# Display the 32-bit RGBA image
dim = max(xdim, ydim)
fig = figure(title="Recorded Birds in Lekagul",
             x_range=(0,200), y_range=(0,200),
             # Specifying xdim/ydim isn't quire right :-(
             # width=xdim, height=ydim,
             )
fig.image_rgba(image=[img], x=0, y=0, dw=200, dh=200)

fig.yaxis.visible = False
fig.xaxis.visible = False

Dimensions: (906, 908)


In [28]:
birds_name = birds['English_name'].unique()
x = np.linspace(0,100,len(birds_name))
y = np.linspace(0,100,len(birds_name))

colors = [
    "#%02x%02x%02x" % (int(r), int(g), 150) for r, g in zip(50+2*x, 30+2*y)
]
colormap = dict(zip(birds_name, colors))
#colormap = {'setosa': 'red', 'versicolor': 'green', 'virginica': 'blue'}
colors = [colormap[x] for x in birds['English_name']]
TOOLS="hover,crosshair,pan,wheel_zoom,zoom_in,zoom_out,box_zoom,undo,redo,reset,tap,save,box_select,poly_select,lasso_select,"
TOOLS="hover"

In [29]:
source_test = ColumnDataSource(test_birds)
fig.asterisk(' X',' Y', source=source_test, size=20, line_color="green", fill_color="blue", fill_alpha=0.5)

# output the fingure in the notebook
output_notebook()

show(fig)

Loading BokehJS ...

## 2.b Blue Pipits and Kasios birds

In [30]:
blue_pipits = birds[birds['English_name']=='Rose-crested Blue Pipit']
blue_pipits.columns

Index(['File ID', 'English_name', 'Vocalization_type', 'Quality', 'Time',
       'Date', 'X', 'Y', 'Year', 'year', 'colors'],
      dtype='object')

In [33]:
source = ColumnDataSource(blue_pipits)
fig.circle('X','Y', source=source, color="blue", size=8, fill_alpha=0.5)

# output the fingure in the notebook
output_notebook()

show(fig)

Loading BokehJS ...

## 2.c Interactive map with all birds

### To help us visualize the repartition of the birds in an interactive manner, we allow the user to customize the figure by selecting species and years.

In [8]:
# load the libraries
from __future__ import division

import numpy as np
from PIL import Image
from bokeh.plotting import figure, show, output_file, ColumnDataSource
from bokeh.io import output_notebook
from bokeh.models import Slider,RangeSlider, DateRangeSlider, MultiSelect
from bokeh.layouts import column
from bokeh.models import Legend
from bokeh.palettes import Category20
from bokeh.layouts import  widgetbox

In [9]:
# pre-processing for the interactive plot
## create the year of a given date
def conv(x):
    try:
        return int(x)
    except:
        return np.nan
birds['year'] = birds['Date'].apply(lambda x : conv(x[-4:]))
birds.dropna(inplace=True)


## create a color column in the dataframe associated to each specy
name_birds = birds['English_name'].unique()
num_birds = len(birds['English_name'].unique())
dict_colors = dict(zip(name_birds,Category20[num_birds]))
    
birds['colors'] = birds['English_name'].apply(lambda x : dict_colors[x])

In [10]:
def in_name(x, list_input):
    return (x in list_input)

def modify_doc(doc): 
    legend=[]
    # Display the 32-bit RGBA image
    dim = max(xdim, ydim)
    fig = figure(title="test",
                 x_range=(0,250), y_range=(0,200), 
                 tools=TOOLS, width=900
                 )


    fig.image_rgba(image=[img], x=0, y=0, dw=200, dh=200)
    name_birds = birds['English_name'].unique()
    num_birds = len(birds['English_name'].unique())
    
    source = ColumnDataSource(birds)
    source_test = ColumnDataSource(test_birds)
    
    fig.circle('X', 'Y', source=source,size=8, color='colors', fill_alpha=0.7, legend='English_name')
    fig.asterisk(' X',' Y', source=source_test, size=20, line_color="red",line_width=4, fill_alpha=1)
    
    year = 1983
    rangeslider = RangeSlider(title="Date Range", start=1983, end=2018, value=(1983, 2018), step=1, callback_policy='mouseup')
    multiselect = MultiSelect(title = "Select your species : ", value = list(name_birds) , options = list(name_birds) )
    multiselectTest = MultiSelect(title = "Select Kasios recording : ", value = [str(a) for a in test_birds['ID']] , options = [str(a) for a in test_birds['ID']] )
    
    def callback(attr, old, new):
        date_tuple = rangeslider.value
        birds_name = multiselect.value
        dataset = birds[(birds['year']<=date_tuple[1]) & (birds['year']>=date_tuple[0]) & (birds['English_name'].apply(lambda x: in_name(x, birds_name)))]
        new_data = ColumnDataSource(dataset)
        name_birds = birds_name
        source.data =new_data.data
    
    def update_kasios(attr, old, new):
        test_number = multiselectTest.value
        dataset2 = test_birds[test_birds['ID']==int(test_number[0])]
        new_data2 = ColumnDataSource(dataset2)
        source_test.data = new_data2.data
        
        
    
    multiselect.on_change('value', callback)
    rangeslider.on_change('value', callback)
    multiselectTest.on_change('value', update_kasios)
    inputs = widgetbox(rangeslider, multiselect, multiselectTest)
    #doc.add_root(column(rangeslider, fig))
    doc.add_root(column(inputs, fig))
show(modify_doc)